In [1]:
import numpy as np
import pandas as pd
import pickle

In [2]:
np.random.seed(10)

In [3]:
ratings = pd.read_csv('animelist.csv')
anime_df = pd.read_csv('anime.csv')

In [4]:
ratings

user_id  anime_id  rating  watching_status  watched_episodes
0                0        67       9                1                 1
1                0      6702       7                1                 4
2                0       242      10                1                 4
3                0      4898       0                1                 1
4                0        21      10                1                 0
...            ...       ...     ...              ...               ...
109224742   353404       507       7                2                 2
109224743   353404       392       9                2               112
109224744   353404       882       6                2                 1
109224745   353404       883       8                2                 1
109224746   353404       149       0                6                 0

[109224747 rows x 5 columns]

In [5]:
ratings_current = ratings.loc[ratings['watching_status']==1]

Watching_status
1: Currently Watching
2: Completed
3: On Hold
4: Dropped
6: Plan to Watch

In [6]:
rand_userIds = np.random.choice(ratings_current['user_id'].unique(), 
                                size=int(len(ratings_current['user_id'].unique())*0.3), 
                                replace=False)
ratings_target = ratings_current.loc[ratings_current['user_id'].isin(rand_userIds)]

In [7]:
print(len(rand_userIds))

91032


In [9]:
#load ratings used for training
#ratings_training = pd.read_csv('rating_complete.csv')
ratings_training = ratings.loc[ratings['watching_status']==2]
ratings_training = ratings_training.drop(columns=['watching_status', 'watched_episodes'])
ratings_training = ratings_training.loc[ratings_training['user_id'].isin(rand_userIds)]
ratings_training.loc[:, 'rating'] = 1

In [ ]:
ratings_training.to_csv('ratings_training.csv')

In [10]:
# Get a list of all anime IDs
all_animeIds = ratings['anime_id'].unique()

In [11]:
import torch
from torch.utils.data import Dataset

class AnimeLensTrainDataset(Dataset):
    """AnimeLens PyTorch Dataset for Training
    
    Args:
        ratings (pd.DataFrame): Dataframe containing the anime ratings
        all_animeIds (list): List containing all animeIds
    
    """

    def __init__(self, ratings, all_animeIds):
        self.users, self.items, self.labels = self.get_dataset(ratings, all_animeIds)

    def __len__(self):
        return len(self.users)
  
    def __getitem__(self, idx):
        return self.users[idx], self.items[idx], self.labels[idx]

    def get_dataset(self, ratings, all_animeIds):
        users, items, labels = [], [], []
        user_item_set = set(zip(ratings['user_id'], ratings['anime_id']))

        num_negatives = 4
        for u, i in user_item_set:
            users.append(u)
            items.append(i)
            labels.append(1)
            for _ in range(num_negatives):
                negative_item = np.random.choice(all_animeIds)
                while (u, negative_item) in user_item_set:
                    negative_item = np.random.choice(all_animeIds)
                users.append(u)
                items.append(negative_item)
                labels.append(0)

        return torch.tensor(users), torch.tensor(items), torch.tensor(labels)

In [12]:
import torch.nn as nn
from torch.utils.data import DataLoader

class NCF(nn.Module):
    """ Neural Collaborative Filtering (NCF)
    
        Args:
            num_users (int): Number of unique users
            num_items (int): Number of unique items
            ratings (pd.DataFrame): Dataframe containing the anime ratings for training
            all_animeIds (list): List containing all animeIds (train + test)
    """
    
    def __init__(self, num_users, num_items, ratings, all_animeIds):
        super().__init__()
        #mlp and mf embedding of all users, each embedding having 8 dimensions
        self.user_mlp_embedding = nn.Embedding(num_embeddings=num_users, embedding_dim=8)
        self.user_mf_embedding = nn.Embedding(num_embeddings=num_users, embedding_dim=8)
        #mlp and mf embedding of all animes, each embedding having 8 dimensions
        self.item_mlp_embedding = nn.Embedding(num_embeddings=num_items, embedding_dim=8)
        self.item_mf_embedding = nn.Embedding(num_embeddings=num_items, embedding_dim=8)
        self.fc1 = nn.Linear(in_features=16, out_features=64)
        self.fc2 = nn.Linear(in_features=64, out_features=32)
        self.output = nn.Linear(in_features=40, out_features=1)
        self.ratings = ratings
        self.all_animeIds = all_animeIds
        
    def forward(self, user_input, item_input):
        
        # Pass through embedding layers
        user_mlp_embedded = self.user_mlp_embedding(user_input)
        item_mlp_embedded = self.item_mlp_embedding(item_input)
        
        user_mf_embedded = self.user_mf_embedding(user_input)
        item_mf_embedded = self.item_mf_embedding(item_input)

        # Concat the two mlp embedding layers
        mlp_vector = torch.cat([user_mlp_embedded, item_mlp_embedded], dim=-1)
        
        # Do element-wise multiplication on the two mf embedding layers
        mf_vector = torch.mul(user_mf_embedded, item_mf_embedded)

        # Pass through dense layer
        mlp_vector = nn.ReLU()(self.fc1(mlp_vector))
        mlp_vector = nn.ReLU()(self.fc2(mlp_vector))
        
        # concat mlp and mf vectors
        vector = torch.cat([mlp_vector, mf_vector], dim=-1)

        # Output layer
        pred = nn.Sigmoid()(self.output(vector))

        return pred
    
    def training_step(self, batch, batch_idx):
        user_input, item_input, labels = batch
        predicted_labels = self(user_input, item_input)
        loss = nn.BCELoss()(predicted_labels, labels.view(-1, 1).float())
        return loss

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters())

    def train_dataloader(self):
        return DataLoader(AnimeLensTrainDataset(self.ratings, self.all_animeIds),
                          batch_size=512)

In [13]:
#init model
num_users = ratings['user_id'].max()+1
num_items = ratings['anime_id'].max()+1
all_animeIds = ratings['anime_id'].unique()
model = NCF(num_users, num_items, ratings_training, all_animeIds)

In [15]:
#load train_data
train_data = model.train_dataloader()

In [16]:
#training step
optimizer = model.configure_optimizers()

num_epochs = 2
count = 0
for epoch in range(num_epochs):
    batch_idx = 0
    #training loop
    for train_batch in train_data:
        count += 1
        loss = model.training_step(train_batch, batch_idx)
        if count%1000 == 0:
            print("train_loss: ", loss.item())
            print("batch num: ", count)

        loss.backward()
        optimizer.step()
        optimizer.zero_grad()
        batch_idx += 1

train_loss:  0.21055953204631805
batch num:  1000
train_loss:  0.2262933850288391
batch num:  2000
train_loss:  0.18054954707622528
batch num:  3000
train_loss:  0.2188357412815094
batch num:  4000
train_loss:  0.16918760538101196
batch num:  5000
train_loss:  0.21105481684207916
batch num:  6000
train_loss:  0.2326846420764923
batch num:  7000
train_loss:  0.2151559442281723
batch num:  8000
train_loss:  0.2137231081724167
batch num:  9000
train_loss:  0.2166399210691452
batch num:  10000
train_loss:  0.2336372584104538
batch num:  11000
train_loss:  0.2537859380245209
batch num:  12000
train_loss:  0.20218577980995178
batch num:  13000
train_loss:  0.21719403564929962
batch num:  14000
train_loss:  0.24591757357120514
batch num:  15000
train_loss:  0.21171845495700836
batch num:  16000
train_loss:  0.18553462624549866
batch num:  17000
train_loss:  0.1954098492860794
batch num:  18000
train_loss:  0.18337436020374298
batch num:  19000
train_loss:  0.22787170112133026
batch num:  2000

train_loss:  0.17037418484687805
batch num:  162000
train_loss:  0.163417786359787
batch num:  163000
train_loss:  0.1351500302553177
batch num:  164000
train_loss:  0.13343310356140137
batch num:  165000
train_loss:  0.10796921700239182
batch num:  166000
train_loss:  0.16925206780433655
batch num:  167000
train_loss:  0.17977561056613922
batch num:  168000
train_loss:  0.1532733142375946
batch num:  169000
train_loss:  0.20404265820980072
batch num:  170000
train_loss:  0.13912343978881836
batch num:  171000
train_loss:  0.14896740019321442
batch num:  172000
train_loss:  0.14458483457565308
batch num:  173000
train_loss:  0.14673802256584167
batch num:  174000
train_loss:  0.14146284759044647
batch num:  175000
train_loss:  0.14686539769172668
batch num:  176000
train_loss:  0.149176225066185
batch num:  177000
train_loss:  0.14329499006271362
batch num:  178000
train_loss:  0.16434940695762634
batch num:  179000
train_loss:  0.19444717466831207
batch num:  180000
train_loss:  0.196

train_loss:  0.1547693908214569
batch num:  321000
train_loss:  0.16238735616207123
batch num:  322000
train_loss:  0.22291329503059387
batch num:  323000
train_loss:  0.14914721250534058
batch num:  324000
train_loss:  0.17659151554107666
batch num:  325000
train_loss:  0.16479767858982086
batch num:  326000
train_loss:  0.15852999687194824
batch num:  327000
train_loss:  0.12146740406751633
batch num:  328000
train_loss:  0.16178718209266663
batch num:  329000
train_loss:  0.1616138219833374
batch num:  330000
train_loss:  0.15506035089492798
batch num:  331000
train_loss:  0.14927582442760468
batch num:  332000
train_loss:  0.14721781015396118
batch num:  333000
train_loss:  0.12012237310409546
batch num:  334000
train_loss:  0.18864619731903076
batch num:  335000
train_loss:  0.15812897682189941
batch num:  336000
train_loss:  0.16245347261428833
batch num:  337000
train_loss:  0.15716737508773804
batch num:  338000
train_loss:  0.16668099164962769
batch num:  339000
train_loss:  0

In [17]:
#save model
torch.save(model.state_dict(), "recommender_model_3_3epochs.pt")

In [14]:
#load model
model = NCF(num_users, num_items, ratings_training, all_animeIds)
model.load_state_dict(torch.load("recommender_model_3.pt"))
model.eval()

NCF(
  (user_mlp_embedding): Embedding(353405, 8)
  (user_mf_embedding): Embedding(353405, 8)
  (item_mlp_embedding): Embedding(48493, 8)
  (item_mf_embedding): Embedding(48493, 8)
  (fc1): Linear(in_features=16, out_features=64, bias=True)
  (fc2): Linear(in_features=64, out_features=32, bias=True)
  (output): Linear(in_features=40, out_features=1, bias=True)
)

In [83]:
test_model = NCF(353405, 48493, 0, 0)
test_model.load_state_dict(torch.load("recommender_model_2.pt"))

<All keys matched successfully>

In [71]:
#get a smaller batch of users for testing
test_userIds = np.random.choice(rand_userIds, 
                                size=int(len(rand_userIds)*0.2), 
                                replace=False)

In [72]:
len(test_userIds)

18206

In [73]:
#filter test ratings based on new user batch
ratings_test_users = ratings.loc[ratings['user_id'].isin(test_userIds)]
ratings_target = ratings_target.loc[ratings_target['user_id'].isin(test_userIds)]

In [74]:
#get only 1 review per user for testing
ratings_target['rank_latest'] = ratings_target.groupby(['user_id'])['watching_status'].rank(method='first', ascending=False)
ratings_target = ratings_target.loc[ratings_target['rank_latest']==1]

In [75]:
# User-item pairs for testing
test_user_item_set = set(zip(ratings_target['user_id'], ratings_target['anime_id']))

# Dict of all items that are interacted with by each user
print("A")
ratings_interacted = ratings_test_users.loc[ratings_test_users['watching_status']!=4]
user_interacted_items = ratings_interacted.groupby('user_id')['anime_id'].apply(list).to_dict()
print("B")

hits = []
count = 0
for (u,i) in test_user_item_set:
    interacted_items = user_interacted_items[u]
    not_interacted_items = set(all_animeIds) - set(interacted_items)
    selected_not_interacted = list(np.random.choice(list(not_interacted_items), 99))
    test_items = selected_not_interacted + [i]
    
    predicted_labels = np.squeeze(model(torch.tensor([u]*100), 
                                        torch.tensor(test_items)).detach().numpy())
    print(predicted_labels)
    
    top10_items = [test_items[i] for i in np.argsort(predicted_labels)[::-1][0:10].tolist()]
    
    if i in top10_items:
        hits.append(1)
    else:
        hits.append(0)
    count += 1
    print(count)
        
print("The Hit Ratio @ 10 is {:.2f}".format(np.average(hits)))

A
B
[8.9921593e-04 8.2516801e-03 4.9350201e-03 6.9211703e-03 1.0390095e-03
 3.1174102e-05 1.5104208e-04 5.2674492e-03 9.8624572e-05 2.0199304e-04
 2.0774098e-03 5.9417393e-03 1.1980226e-05 8.8463050e-05 3.7971855e-04
 6.5788685e-04 1.1312417e-03 1.7709755e-03 2.9343271e-04 4.3443535e-03
 9.5494968e-08 7.9871861e-05 9.8690437e-04 3.5359552e-03 3.7610651e-05
 7.6412696e-05 4.6049822e-03 5.2497203e-06 1.1176397e-05 9.7040675e-04
 1.2281000e-04 1.3232839e-03 2.3430309e-04 6.8503050e-06 1.4333799e-05
 5.3734675e-02 1.9318094e-04 2.3314431e-04 9.8164822e-04 1.2690779e-04
 4.5661160e-04 6.1342862e-06 9.4760545e-02 2.2176523e-03 1.6175129e-02
 5.1421596e-04 9.9180581e-04 6.5849799e-06 1.3764859e-03 9.8028669e-11
 2.2004554e-03 3.1511907e-03 2.6901837e-03 2.3286506e-04 7.1204721e-04
 1.6502339e-02 1.0240731e-04 1.3023608e-03 1.9153392e-04 2.3946952e-06
 1.1806558e-04 3.8023302e-06 2.6055051e-03 3.5853669e-02 7.6290162e-05
 2.5309565e-02 3.2856315e-05 8.6413254e-04 9.6754013e-03 5.0973101e-03
 8

[1.00973889e-03 9.47825611e-03 9.31092724e-03 8.05820629e-04
 4.64596640e-04 2.39596376e-03 7.75331515e-04 4.67189733e-04
 3.66274180e-05 2.88094125e-05 1.12186695e-04 3.01467860e-03
 6.69841465e-05 2.91985050e-02 1.48741459e-03 1.04118371e-04
 4.59728623e-03 8.11264676e-04 1.32514932e-03 8.43598042e-03
 2.10342603e-03 8.24025774e-05 4.11355607e-02 6.94431947e-05
 4.18916857e-03 9.76862945e-03 6.44079037e-03 1.39759824e-04
 4.55613743e-04 8.68431106e-03 1.09870257e-02 2.07929668e-04
 2.64916359e-03 5.68195595e-04 1.73881213e-04 2.62736715e-03
 2.89531337e-04 6.12803095e-04 5.10596260e-02 2.45442847e-03
 8.29675607e-03 2.19105813e-03 9.50395188e-05 1.82418560e-03
 5.08030585e-04 3.12708244e-02 1.68884126e-03 8.29323195e-04
 3.28212082e-02 7.19393836e-04 3.49717624e-02 3.85372114e-04
 6.54811098e-04 4.03406848e-05 2.41270158e-02 9.58027132e-03
 4.69594932e-04 3.06509755e-04 2.20381864e-03 1.47680873e-02
 2.86445254e-04 1.67865551e-03 3.27723574e-05 9.74834373e-04
 1.16729049e-03 3.069697

[2.40426394e-03 2.72970442e-02 1.35145476e-03 7.95417186e-03
 3.43516748e-03 4.89444565e-03 1.40566000e-04 5.20631718e-03
 1.59127750e-02 6.52362127e-03 1.33582456e-02 1.03583626e-01
 2.03020480e-02 1.65837293e-03 1.46558927e-02 4.17924253e-03
 7.17377337e-03 7.06520900e-02 7.83587396e-02 2.85723782e-03
 3.87761323e-03 1.00352298e-02 7.85719693e-01 9.96393428e-05
 1.27601868e-03 4.53281915e-03 1.02807824e-02 2.02173088e-02
 6.02388289e-04 7.06865510e-04 3.81497171e-04 1.77939655e-03
 3.63615621e-03 3.23623390e-04 8.82377644e-05 3.40891033e-02
 5.37811022e-04 6.99943257e-03 1.55650589e-04 8.31428741e-04
 8.99794698e-03 8.17326305e-04 1.72881410e-02 3.36240269e-02
 4.30989685e-03 2.26372276e-02 2.13381369e-04 1.00998662e-01
 1.23158814e-02 1.47539715e-03 8.53544043e-04 1.20119262e-03
 1.12989089e-02 4.04313207e-02 1.06520327e-02 5.95018873e-03
 2.48001423e-03 2.72733951e-03 1.62290921e-03 5.08142225e-02
 2.21501710e-03 5.47886919e-03 2.41539516e-02 1.04189729e-02
 7.08687352e-04 3.650892

[1.59341755e-04 8.97584856e-02 1.17049157e-03 9.43340175e-03
 4.96981233e-01 1.24535989e-04 1.05742551e-03 5.24555624e-04
 6.11785916e-04 2.99191568e-02 3.57307552e-04 1.36102112e-02
 2.80234171e-03 1.83705546e-04 2.23901775e-02 2.22276777e-01
 3.95862106e-03 9.26956069e-04 1.83119543e-03 2.57542427e-03
 1.04135172e-02 5.57035534e-03 2.67244468e-04 2.93570478e-02
 6.28987502e-04 8.95252626e-04 5.97468053e-04 1.59928005e-03
 3.15253437e-03 7.21129701e-02 7.91565608e-03 1.57959647e-02
 1.43136736e-03 2.73748231e-03 8.84771906e-03 2.78424263e-01
 9.49557781e-01 1.51075879e-02 4.61886259e-04 1.36156708e-01
 9.66061896e-04 1.66589841e-02 3.83002050e-02 2.30704714e-03
 7.61235242e-07 2.72162980e-03 3.87900844e-02 1.68362055e-02
 1.34726020e-03 5.80200367e-03 1.93048781e-03 2.57868879e-02
 6.92668080e-04 2.51569058e-04 1.71752200e-02 1.82749573e-04
 7.34826922e-02 4.59873672e-06 7.37509504e-03 5.88289229e-03
 4.05774917e-03 2.59878393e-03 2.72728223e-03 2.17134375e-02
 2.18810281e-03 1.046027

[4.22742032e-03 7.30540254e-04 2.90210079e-02 1.42968653e-04
 1.08205283e-03 1.07416719e-01 4.23200574e-04 3.03857214e-05
 1.54634457e-04 3.80623504e-04 6.28125621e-03 3.99433300e-02
 6.14940946e-04 9.52084316e-04 1.57385750e-03 2.53420952e-03
 9.33577947e-04 5.86536229e-01 2.19834992e-03 1.54031237e-04
 1.46169087e-03 2.89025693e-03 1.76313648e-03 1.89013674e-03
 2.44423834e-04 6.99565560e-03 3.66664007e-02 1.61465090e-02
 3.21509782e-04 3.14295269e-03 7.60958530e-03 1.10420435e-04
 1.50595210e-03 1.45853944e-02 4.30490077e-03 1.90755512e-04
 2.89430935e-02 4.15991805e-02 1.06059446e-03 3.29472800e-03
 1.18267052e-02 7.30140209e-02 5.97791150e-05 6.58821780e-04
 3.99711367e-04 5.44040790e-03 1.73185125e-03 1.88906908e-01
 3.75183374e-02 4.48184408e-04 4.90927370e-04 6.46262290e-03
 3.70206748e-04 6.26637973e-03 1.37351497e-04 9.79335280e-04
 1.92014258e-02 1.24582155e-02 2.54408712e-03 1.13839691e-03
 3.76123702e-04 4.60713767e-02 3.08142335e-04 8.56945198e-03
 4.28589992e-03 2.219530

...

3502
[5.04162833e-02 2.91985460e-04 6.94102084e-04 5.35500469e-03
 3.28456008e-05 2.50590441e-04 4.10660682e-03 8.37106351e-03
 3.71793343e-04 9.48321879e-01 2.72872881e-03 1.00804144e-03
 1.60050318e-02 8.07382399e-04 5.15484542e-04 1.19108511e-02
 2.26867211e-04 2.82117166e-03 4.11621243e-01 1.12258713e-03
 9.85374302e-02 1.75178458e-03 1.05958981e-02 7.60024297e-04
 1.67225822e-04 1.00259706e-04 2.02114478e-01 5.89010597e-04
 1.14211708e-03 3.27859051e-03 9.05515568e-04 3.40049481e-03
 2.27808487e-03 4.14900496e-05 9.88699496e-03 2.05584196e-03
 1.69524143e-03 1.07848209e-04 1.47577673e-02 7.68546527e-03
 1.28504817e-05 5.18881076e-04 2.09776661e-03 1.44523254e-03
 1.20462780e-03 2.56311469e-04 5.58211759e-04 6.96501404e-04
 1.67928021e-02 1.12279784e-03 1.00418332e-03 8.24954640e-03
 4.88921127e-04 1.46912032e-06 1.80682517e-04 1.51483319e-03
 5.04061487e-03 8.57792702e-03 3.47345416e-03 1.59149501e-03
 1.66839138e-02 6.59856480e-03 4.84969728e-02 2.94887694e-03
 7.16583757e-03 3.3

[1.9567441e-03 7.6660020e-03 7.6867163e-04 4.1719675e-03 3.4561059e-03
 3.0698210e-03 7.3878634e-01 8.8801852e-04 1.0169000e-02 9.3636621e-04
 1.6887991e-02 2.4730903e-03 2.1612800e-03 5.4932486e-02 1.9066890e-03
 1.0793652e-02 7.9427083e-04 1.1818267e-06 1.9370811e-02 6.8771760e-03
 3.5827481e-03 2.6247073e-02 5.3875586e-03 1.3229243e-02 3.1245038e-02
 5.6187395e-02 2.3976939e-02 2.0883942e-06 2.9874867e-04 2.5386255e-02
 1.1869462e-02 7.2863346e-01 1.6476945e-03 3.0106511e-03 2.1847513e-02
 5.0045610e-03 2.2510975e-03 6.1741835e-03 1.6909650e-03 7.9644158e-02
 1.0794541e-03 1.6658204e-02 4.7051534e-03 5.2046552e-03 7.4686524e-03
 2.6163150e-02 1.3404706e-02 2.3611000e-02 3.2440507e-01 9.9895718e-03
 1.3536790e-02 9.0818899e-04 5.5003256e-02 2.7287629e-01 1.5616723e-02
 7.8621805e-03 2.1616665e-05 2.7136365e-03 5.1090349e-03 1.5220830e-02
 2.5741605e-03 6.4483953e-01 3.2664125e-04 1.2662268e-03 3.4623026e-05
 9.7936147e-04 7.8382036e-03 9.1897392e-01 1.2664535e-03 4.1099446e-04
 1.185

3561
[3.26111633e-03 1.53022725e-02 6.20180322e-03 9.63738770e-04
 5.56384027e-03 1.29015315e-02 9.99651104e-03 4.30225907e-03
 1.14640921e-01 7.80196814e-03 4.79863673e-01 2.04636552e-03
 6.01965294e-04 1.09362940e-03 3.15626239e-05 1.61421914e-02
 2.21741712e-03 1.78577434e-02 3.04409047e-03 3.14088626e-04
 7.61027634e-02 2.59455672e-04 2.55212956e-03 1.10661716e-03
 2.60450761e-04 1.37500546e-03 1.49983069e-04 3.44510947e-04
 8.63582711e-04 1.11979870e-02 2.18080837e-04 1.24379052e-02
 6.45010686e-03 2.92350654e-04 7.67505728e-03 2.88111940e-02
 7.95469852e-04 4.77875629e-03 1.59142539e-02 3.69116751e-04
 9.48816389e-02 2.19228417e-02 5.01434726e-04 5.96702173e-02
 2.24248064e-03 2.48905681e-02 3.34738381e-02 4.66159033e-03
 4.68320260e-03 1.55488076e-02 5.08045137e-04 4.43290640e-03
 6.24052295e-03 4.02293867e-03 7.17550069e-02 3.78499203e-03
 7.67035177e-03 1.12910219e-01 1.27647212e-03 5.00978960e-04
 2.44790060e-03 1.85218145e-04 5.70628010e-02 9.09101497e-03
 3.74697056e-03 4.2

[3.72727300e-05 1.55623184e-05 7.24978381e-05 7.70533370e-06
 1.56170483e-06 4.72732199e-06 2.62131070e-05 5.19440579e-09
 1.59757081e-04 3.96455835e-05 3.24790199e-05 5.72166580e-04
 1.92255902e-05 1.95976245e-04 2.63397279e-03 1.55587568e-05
 2.64566370e-05 1.91308318e-05 2.31110280e-05 3.44382897e-05
 5.22195405e-05 1.17858211e-02 1.48269848e-03 8.08494951e-06
 5.87017666e-06 2.37098698e-06 4.11749606e-05 1.76372416e-02
 6.70728623e-05 1.74793047e-06 2.19878511e-05 9.72793810e-03
 5.04257841e-05 2.98938867e-05 1.23417522e-05 3.21139014e-05
 6.37596124e-04 2.82249792e-04 2.74126796e-05 1.71021850e-06
 4.25215367e-05 1.92116545e-06 6.20292558e-05 4.07055995e-05
 5.24097641e-06 1.12433936e-05 4.37596493e-04 1.12081725e-05
 6.38670754e-05 6.53197467e-02 7.52952415e-04 3.63211147e-05
 1.69856532e-04 8.46056282e-05 9.09428636e-05 2.54510101e-02
 1.75041600e-06 1.54524343e-04 1.84211312e-05 2.96967861e-04
 3.26944370e-04 3.49586189e-04 1.36462739e-04 1.00407651e-05
 1.73754200e-01 2.016970

[4.60664369e-03 4.72773192e-03 2.70106201e-03 3.42600718e-02
 6.83566043e-03 3.63947712e-02 1.20009771e-02 1.33999772e-02
 2.44913734e-02 7.08143925e-03 5.59851676e-02 2.93364457e-04
 5.62997186e-04 9.94888251e-04 2.35990202e-03 6.82827691e-03
 2.52063144e-02 1.23919630e-02 1.52656529e-03 7.92800100e-04
 5.68857242e-04 7.58444134e-04 4.30152789e-02 1.23663191e-02
 5.09949803e-01 1.99564197e-03 2.94949533e-03 2.97024176e-02
 7.36869546e-03 1.63304824e-02 1.61465094e-03 4.42206524e-02
 9.18648147e-04 2.27959119e-02 1.95037632e-03 1.78500044e-03
 3.58106382e-02 1.46279088e-03 6.47758180e-03 2.68120621e-03
 2.33812514e-03 5.47782741e-02 3.71310790e-03 5.65469358e-03
 5.95349818e-03 9.80854617e-04 4.85094488e-02 5.27639117e-04
 2.42378712e-02 4.45607118e-04 1.24520436e-03 4.84612919e-02
 2.92480545e-04 7.28676608e-03 9.96811432e-04 8.88572074e-04
 1.01662844e-01 2.97098444e-03 1.66691327e-03 3.31349522e-02
 4.68647152e-01 1.30514975e-03 7.55847152e-03 1.97374518e-03
 3.03233066e-03 6.480473

In [42]:
def create_user_vector(user_id, ratings_completed, num_anime):
    #user_id: id of user
    #ratings_completed: pandas dataframe of anime reviews with completed watching status and rating != 0
    #num_anime: total number of animes in the dataset
    user_rating = ratings_completed.loc[ratings_completed['user_id']==user_id]
    user_anime = user_rating['anime_id']
    user_vector = np.zeros(num_anime)
    for anime in user_anime:
        anime_id = anime_df[anime_df['MAL_ID'] == anime].index[0]
        user_vector[anime_id] = 1
    return user_vector

def get_user_anime_set(user_id, ratings_completed, anime_df):
    #user_id: id of user
    #ratings_completed: pandas dataframe of anime reviews with completed watching status and rating != 0
    #anime_df: pandas dataframe of all animes and its features
    user_rating = ratings_completed.loc[ratings_completed['user_id']==user_id]
    user_anime = user_rating['anime_id']
    user_set = set()
    for anime in user_anime:
        anime_id = anime_df[anime_df['MAL_ID'] == anime].index[0]
        user_set.add(anime_id)
    return user_set


def create_user_set_dict(ratings):
    #ratings: pandas dataframe of anime reviews
    #num_anime: total number of animes in the dataset
    #anime_df: pandas dataframe of all animes and its features
    user_set_dict = {}
    for review in ratings.itertuples():
        if review[1] in user_set_dict:
            user_set_dict[review[1]].add(review[2])
        else:
            user_set_dict[review[1]] = {review[2]}
    return user_set_dict

In [43]:
ratings_training

user_id  anime_id  rating
11               0        68       1
12               0      1689       1
13               0      2913       1
14               0      1250       1
15               0       356       1
...            ...       ...     ...
109224358   353400     16417       1
109224359   353400     35790       1
109224360   353400     38826       1
109224361   353400     16870       1
109224362   353400       523       1

[19701116 rows x 3 columns]

In [18]:
len(ratings_training['user_id'].unique())

89828

In [34]:
user_set_dict = create_user_set_dict(ratings_training)

In [90]:
#save user_set_dict in a pickle file
with open('user_set_dict.pickle', 'wb') as handle:
    pickle.dump(user_set_dict, handle, protocol=pickle.DEFAULT_PROTOCOL)

In [20]:
#load user_set_dict from pickle file
with open('user_set_dict.pickle', 'rb') as handle:
    user_set_dict = pickle.load(handle)

In [19]:
def find_closest_user(user_anime, user_set_dict):
    #user_anime: list of anime Ids active user interacted with
    #user_set_dict: dict of userID to their set of animes watched

    active_user_set = set(user_anime)
    
    closest_user = 0
    closest_distance = float('inf')
    for user in user_set_dict.keys():
        distance = len(active_user_set.symmetric_difference(user_set_dict[user]))
        if distance < closest_distance:
            closest_user = user
            closest_distance = distance
    return closest_user, closest_distance

In [21]:
my_vector = [80, 81, 82, 83, 854, 85, 86, 87, 88, 91, 93, 1090, 1091, 1092, 2294, 2581, 3927, 6636]
closest_user = find_closest_user(my_vector, user_set_dict)

In [22]:
closest_user

(1623, 17)

In [23]:
predicted_label = model(torch.tensor(closest_user[0]), torch.tensor(1535))
predicted_label.item()

0.9518963098526001

In [68]:
np.squeeze(model(torch.tensor(0), torch.tensor(6636)))

tensor(0.0028, grad_fn=<SqueezeBackward0>)

In [24]:
shounen_vector = [20, 1735, 269, 6702, 22043, 22319, 36511, 5114, 2001, 249, 136, 137, 138, 139, 223, 813, 3588, 21, 288, 392, 482, 14513, 18115, 235, 24833, 30654, 665, 666, 3603, 14719, 20899, 26055, 9919, 1604]
closest_user = find_closest_user(shounen_vector, user_set_dict)
top10_items = recommend_anime(model, closest_user[0], all_animeIds, anime_df, shounen_vector)

['Toradora!', 'Angel Beats!', 'Ore no Imouto ga Konnani Kawaii Wake ga Nai', 'Shingeki no Kyojin', 'Sword Art Online', 'Mirai Nikki', 'Mahou Shoujo Madoka★Magica', 'Ano Hi Mita Hana no Namae wo Bokutachi wa Mada Shiranai.', 'Elfen Lied', 'Tensei shitara Slime Datta Ken']


In [22]:
def print_anime(anime_list, anime_df):
    anime_name_list = list()
    for anime in anime_list:
        anime_name_list.append(anime_df.loc[anime_df['MAL_ID'] == anime]['Name'].item())
    print(anime_name_list)
    return(anime_name_list)

In [23]:
def recommend_anime(model, user_id, all_animeIds, anime_df, user_watched = set(), num_recommend = 10):
    #model: NCF model used for recommendation
    #user_id: integer value representing a user
    #all_animeIds: set of all anime Ids
    #user_watched: set of all anime watched by active user
    #num_recommend: number of animes returned by the function
    non_interacted = set(all_animeIds)-set(user_watched)
    non_interacted = list(non_interacted)
    predicted_labels = np.squeeze(model(torch.tensor([user_id]*len(non_interacted)), 
                                        torch.tensor(non_interacted)).detach().numpy())
    recommended_anime = [non_interacted[x] for x in np.argsort(predicted_labels)[::-1][0:num_recommend].tolist()]
    recommended_anime = print_anime(recommended_anime, anime_df)
    return recommended_anime

In [25]:
user_vector = []
closest_user = find_closest_user(user_vector, user_set_dict)
top10_items = recommend_anime(model, closest_user[0], all_animeIds, anime_df)

['Ao no Exorcist', 'No Game No Life', 'Magi: The Labyrinth of Magic', 'Toaru Majutsu no Index', 'Hoshi no Koe', 'Gintama', 'Gyakkyou Burai Kaiji: Ultimate Survivor', 'Naruto', 'Highschool of the Dead', 'Re:Zero kara Hajimeru Isekai Seikatsu']


In [76]:
top10_items

[18679, 63, 61, 31994, 18115, 5233, 297, 1773, 36848, 21235]

In [51]:
rand_userIds

array([330288,  78258, 194474, ..., 191599,  65525,  66899], dtype=int64)

In [26]:
romcom_vector = [4224, 59, 120, 853, 13659, 18857, 14813, 23847, 39547, 18897, 27787, 17895, 2167, 4181, 34280, 8525, 10080, 15117, 16706, 28677, 15809, 48413, 13759, 7054, 9989, 28851, 23273, 37999, 40591, 35968]
closest_user = find_closest_user(romcom_vector, user_set_dict)
top10_items = recommend_anime(model, closest_user[0], all_animeIds, anime_df, romcom_vector, 30)

['Steins;Gate', 'Kimi no Na wa.', 'One Punch Man', 'Death Note', 'Code Geass: Hangyaku no Lelouch', 'Sen to Chihiro no Kamikakushi', 'Ao no Exorcist: Kyoto Fujouou-hen', 'Bakemonogatari', 'Basilisk: Kouga Ninpou Chou', 'Kuroshitsuji: Book of Circus', "Gintama'", 'Durarara!!', 'Kobayashi-san Chi no Maid Dragon: Valentine, Soshite Onsen! - Amari Kitai Shinaide Kudasai', 'Jibaku Shounen Hanako-kun', 'Neon Genesis Evangelion', 'School Rumble', 'Hentai Ouji to Warawanai Neko.', 'Shakugan no Shana', 'Watashi ga Motenai no wa Dou Kangaetemo Omaera ga Warui!', 'Nande Koko ni Sensei ga!?', 'Aki-Sora', 'Sekirei: Pure Engagement', 'Maria†Holic', 'Zero no Tsukaima', 'Amagami SS+ Plus: Extra Episode+ Plus', 'Ookami to Koushinryou', 'One Punch Man 2nd Season', 'Initial D Fourth Stage', 'Kuroko no Basket', 'Fate/stay night']


In [28]:
closest_user

(209774, 27)

In [28]:
print_anime(list(ratings_training.loc[ratings_training['user_id'] == closest_user[0]]['anime_id']), anime_df)

['Kami nomi zo Shiru Sekai', 'Kami nomi zo Shiru Sekai II', 'Kami nomi zo Shiru Sekai: 4-nin to Idol', 'Kami nomi zo Shiru Sekai: Flag 0', 'Kami nomi zo Shiru Sekai: Megami-hen', 'Kami nomi zo Shiru Sekai: Tenri-hen', 'Koe no Katachi']


['Kami nomi zo Shiru Sekai',
 'Kami nomi zo Shiru Sekai II',
 'Kami nomi zo Shiru Sekai: 4-nin to Idol',
 'Kami nomi zo Shiru Sekai: Flag 0',
 'Kami nomi zo Shiru Sekai: Megami-hen',
 'Kami nomi zo Shiru Sekai: Tenri-hen',
 'Koe no Katachi']

In [91]:
anime_df

MAL_ID                             Name    Score  \
0           1                     Cowboy Bebop     8.78   
1           5  Cowboy Bebop: Tengoku no Tobira     8.39   
2           6                           Trigun     8.24   
3           7               Witch Hunter Robin     7.27   
4           8                   Bouken Ou Beet     6.98   
...       ...                              ...      ...   
17557   48481  Daomu Biji Zhi Qinling Shen Shu  Unknown   
17558   48483                     Mieruko-chan  Unknown   
17559   48488  Higurashi no Naku Koro ni Sotsu  Unknown   
17560   48491      Yama no Susume: Next Summit  Unknown   
17561   48492                    Scarlet Nexus  Unknown   

                                                 Genders  \
0        Action, Adventure, Comedy, Drama, Sci-Fi, Space   
1                  Action, Drama, Mystery, Sci-Fi, Space   
2      Action, Sci-Fi, Adventure, Comedy, Drama, Shounen   
3      Action, Mystery, Police, Supernatural, Drama, ...   
4              Adventure, Fantasy, Shounen, Supernatural   
...                                                  ...   
17557                   Adventure, Mystery, Supernatural   
17558                       Comedy, Horror, Supernatural   
17559  Mystery, Dementia, Horror, Psychological, Supe...   
17560                   Adventure, Slice of Life, Comedy   
17561                                    Action, Fantasy   

                          English name                     Japanese name  \
0                         Cowboy Bebop                         カウボーイビバップ   
1               Cowboy Bebop:The Movie                    カウボーイビバップ 天国の扉   
2                               Trigun                             トライガン   
3                   Witch Hunter Robin  Witch Hunter ROBIN (ウイッチハンターロビン)   
4               Beet the Vandel Buster                            冒険王ビィト   
...                                ...                               ...   
17557                          Unknown                         盗墓笔记之秦岭神树   
17558                          Unknown                           見える子ちゃん   
17559  Higurashi:When They Cry – SOTSU                        ひぐらしのなく頃に卒   
17560                          Unknown                ヤマノススメ Next Summit   
17561                          Unknown                     SCARLET NEXUS   

        Type Episodes                         Aired    Premiered  ...  \
0         TV       26   Apr 3, 1998 to Apr 24, 1999  Spring 1998  ...   
1      Movie        1                   Sep 1, 2001      Unknown  ...   
2         TV       26   Apr 1, 1998 to Sep 30, 1998  Spring 1998  ...   
3         TV       26   Jul 2, 2002 to Dec 24, 2002  Summer 2002  ...   
4         TV       52  Sep 30, 2004 to Sep 29, 2005    Fall 2004  ...   
...      ...      ...                           ...          ...  ...   
17557    ONA  Unknown              Apr 4, 2021 to ?      Unknown  ...   
17558     TV  Unknown                     2021 to ?      Unknown  ...   
17559     TV  Unknown                Jul, 2021 to ?  Summer 2021  ...   
17560     TV  Unknown                       Unknown      Unknown  ...   
17561     TV  Unknown                Jul, 2021 to ?  Summer 2021  ...   

       Score-10   Score-9   Score-8  Score-7  Score-6  Score-5  Score-4  \
0      229170.0  182126.0  131625.0  62330.0  20688.0   8904.0   3184.0   
1       30043.0   49201.0   49505.0  22632.0   5805.0   1877.0    577.0   
2       50229.0   75651.0   86142.0  49432.0  15376.0   5838.0   1965.0   
3        2182.0    4806.0   10128.0  11618.0   5709.0   2920.0   1083.0   
4         312.0     529.0    1242.0   1713.0   1068.0    634.0    265.0   
...         ...       ...       ...      ...      ...      ...      ...   
17557   Unknown   Unknown   Unknown      1.0  Unknown  Unknown  Unknown   
17558   Unknown   Unknown   Unknown  Unknown  Unknown  Unknown  Unknown   
17559       1.0   Unknown   Unknown  Unknown  Unknown  Unknown  Unknown   
17560   Unknown   Unknown   Unknown  

In [95]:
#create MAL_ID to anime name dictionary
anime_dict = {}

for anime in anime_df.itertuples():
    anime_dict[anime[1]] = anime[2]
    
#save dict in pickle file
with open('anime_dict.pickle', 'wb') as handle:
    pickle.dump(anime_dict, handle, protocol=pickle.DEFAULT_PROTOCOL)

In [107]:
count = 0
anime_freq_dict = {}
for review in ratings_training.itertuples():
    count += 1
    if review[2] in anime_freq_dict:
        anime_freq_dict[review[2]] += 1
    else:
        anime_freq_dict[review[2]] = 1
print(count)

19701116


In [108]:
for pair in anime_freq_dict.items():
    print(pair)

(68, 8527)
(1689, 27899)
(2913, 71)
(1250, 3889)
(356, 24705)
(121, 32045)
(430, 15089)
(1829, 5772)
(1571, 7145)
(578, 16828)
(431, 30416)
(2762, 342)
(570, 4740)
(3418, 35)
(3010, 580)
(1004, 6376)
(433, 7863)
(600, 630)
(2034, 15244)
(164, 28735)
(4086, 114)
(457, 12361)
(20, 40823)
(1074, 4767)
(761, 5290)
(2248, 5305)
(597, 9387)
(1047, 1966)
(459, 5572)
(466, 2116)
(2543, 384)
(419, 2340)
(199, 41816)
(169, 6779)
(2547, 797)
(174, 7010)
(448, 3033)
(2236, 25114)
(415, 1683)
(1894, 4318)
(22199, 30993)
(6547, 44885)
(9919, 34776)
(5081, 31071)
(31043, 33817)
(31964, 40191)
(33486, 33347)
(36456, 26018)
(38408, 16120)
(28755, 10183)
(1575, 43613)
(35849, 18267)
(1535, 57807)
(18689, 4278)
(38731, 1274)
(30230, 3074)
(38691, 16875)
(38671, 11123)
(40956, 4750)
(5114, 42331)
(37349, 16188)
(20583, 24329)
(28891, 19797)
(32935, 17108)
(38883, 9277)
(40776, 5967)
(37259, 3723)
(11061, 25526)
(37497, 4823)
(37999, 19763)
(40221, 11308)
(37965, 4308)
(18679, 26897)
(38000, 25416)
(32281,

(2397, 3877)
(41053, 887)
(5155, 398)
(25313, 1647)
(32122, 1328)
(19115, 851)
(37989, 3714)
(38710, 453)
(40059, 1882)
(37884, 776)
(5041, 1280)
(2004, 379)
(38733, 2069)
(38972, 864)
(6553, 1530)
(3392, 1992)
(4262, 2248)
(2157, 217)
(5079, 3791)
(963, 3207)
(13203, 1615)
(3965, 2373)
(9999, 2493)
(3848, 3219)
(2680, 2017)
(2386, 2955)
(5530, 11068)
(161, 2139)
(8456, 887)
(33569, 1845)
(33142, 2624)
(34494, 2484)
(35994, 6359)
(4015, 3985)
(517, 4226)
(6973, 1172)
(8800, 365)
(3420, 3396)
(4715, 1559)
(36106, 4083)
(27957, 4305)
(8026, 435)
(5118, 5175)
(6162, 1045)
(13675, 540)
(391, 1213)
(6046, 2327)
(2500, 449)
(10629, 233)
(30641, 642)
(37007, 1823)
(38295, 1454)
(39574, 342)
(37964, 1100)
(38098, 466)
(38397, 4851)
(36653, 2214)
(39324, 3415)
(39710, 4761)
(13859, 2048)
(1675, 615)
(25687, 4225)
(1132, 5736)
(144, 2518)
(704, 960)
(80, 3117)
(6288, 3104)
(90, 5222)
(31251, 4489)
(2363, 1569)
(1526, 5539)
(4793, 3024)
(2263, 973)
(508, 1802)
(856, 5222)
(482, 5356)
(763, 1788)


(40239, 929)
(33728, 800)
(33729, 592)
(33730, 527)
(33242, 753)
(41008, 308)
(39480, 200)
(36950, 533)
(38045, 46)
(37843, 32)
(36745, 71)
(36747, 69)
(34052, 76)
(30234, 148)
(29347, 194)
(15527, 67)
(28789, 971)
(24181, 118)
(41204, 106)
(41189, 66)
(7809, 124)
(10979, 179)
(32853, 74)
(36089, 42)
(38712, 60)
(39057, 159)
(29902, 65)
(22831, 276)
(36182, 53)
(39093, 303)
(29980, 218)
(2796, 302)
(9056, 700)
(35410, 41)
(28241, 84)
(12501, 583)
(32295, 67)
(12865, 182)
(30446, 34)
(29850, 76)
(5304, 149)
(14231, 90)
(38906, 72)
(36001, 1043)
(40292, 67)
(5270, 384)
(33903, 71)
(36092, 35)
(37545, 33)
(9595, 77)
(33245, 244)
(35923, 240)
(31139, 611)
(6462, 127)
(35388, 34)
(35402, 84)
(30431, 53)
(19217, 119)
(39975, 82)
(10516, 341)
(25971, 48)
(40033, 29)
(10436, 90)
(36228, 134)
(27757, 26)
(32289, 96)
(6721, 157)
(37589, 142)
(32789, 59)
(39890, 33)
(32779, 43)
(34997, 29)
(33820, 297)
(23627, 147)
(38554, 34)
(35933, 43)
(35651, 33)
(8701, 137)
(35553, 35)
(4099, 108)
(35709, 81

(41317, 34)
(40197, 165)
(31521, 459)
(41124, 180)
(35776, 150)
(41372, 551)
(41688, 129)
(20971, 815)
(37139, 553)
(37983, 990)
(38026, 128)
(40321, 12)
(1028, 440)
(38410, 235)
(36789, 108)
(964, 359)
(1039, 269)
(625, 149)
(3192, 71)
(39477, 296)
(37180, 10)
(38740, 144)
(4907, 19)
(37897, 986)
(39584, 188)
(35135, 95)
(37044, 122)
(33562, 76)
(36544, 35)
(33266, 16)
(33801, 24)
(33969, 182)
(33702, 41)
(29089, 302)
(36160, 142)
(40602, 851)
(38895, 233)
(36624, 27)
(36756, 152)
(39610, 337)
(36636, 21)
(33564, 223)
(33273, 20)
(35328, 76)
(30573, 176)
(36309, 345)
(37595, 124)
(37742, 105)
(34548, 34)
(34765, 23)
(34762, 21)
(31530, 128)
(35516, 19)
(37997, 352)
(35999, 26)
(33045, 337)
(34771, 118)
(34766, 105)
(32613, 294)
(34140, 28)
(34153, 32)
(37279, 18)
(36914, 569)
(33456, 689)
(36833, 538)
(38897, 304)
(36629, 94)
(34746, 13)
(33912, 66)
(33911, 83)
(36797, 93)
(37265, 63)
(37663, 101)
(37247, 371)
(27907, 183)
(35982, 345)
(38744, 58)
(38254, 403)
(39605, 323)
(40154, 176

(38757, 22)
(42636, 10)
(37318, 59)
(42617, 10)
(38506, 20)
(38290, 22)
(43704, 13)
(35534, 14)
(42863, 8)
(42256, 10)
(39861, 19)
(42646, 10)
(35958, 28)
(43292, 10)
(38326, 16)
(28685, 28)
(29667, 20)
(37692, 20)
(8733, 38)
(38384, 9)
(40559, 42)
(38987, 39)
(41448, 8)
(36358, 12)
(35322, 14)
(39787, 19)
(40905, 10)
(42638, 10)
(15139, 23)
(39284, 39)
(38700, 21)
(42484, 15)
(39854, 18)
(29929, 18)
(40794, 12)
(38640, 11)
(40737, 24)
(36359, 16)
(38549, 45)
(41401, 14)
(39581, 33)
(42547, 5)
(27573, 88)
(39349, 20)
(21037, 13)
(33086, 13)
(36293, 20)
(40430, 18)
(42895, 7)
(19059, 13)
(11445, 59)
(30049, 6)
(30054, 4)
(30122, 11)
(34692, 8)
(40383, 16)
(41451, 10)
(39886, 22)
(38976, 21)
(34426, 13)
(34124, 16)
(40255, 18)
(29917, 23)
(45518, 17)
(21713, 11)
(40171, 19)
(42958, 7)
(41039, 20)
(43917, 9)
(22561, 12)
(36392, 12)
(45616, 13)
(36808, 12)
(33124, 30)
(33916, 4)
(42639, 9)
(37153, 14)
(37464, 14)
(37387, 28)
(42749, 8)
(39225, 7)
(38497, 18)
(42903, 8)
(41174, 35)
(35588, 

(28089, 4)
(33175, 5)
(30932, 1)
(7960, 6)
(39758, 1)
(29487, 1)
(10953, 2)
(28073, 1)
(26133, 5)
(6018, 3)
(24121, 2)
(33913, 2)
(27399, 3)
(33789, 4)
(10856, 2)
(6063, 2)
(40087, 1)
(35270, 2)
(39265, 1)
(39624, 1)
(40316, 1)
(15897, 1)
(31078, 3)
(20005, 3)
(19909, 7)
(42540, 2)
(35034, 1)
(35037, 1)
(35273, 1)
(39488, 2)
(23635, 2)
(38613, 3)
(38614, 4)
(30765, 3)
(34868, 4)
(25983, 3)
(17313, 4)
(17321, 2)
(17317, 2)
(18341, 6)
(34949, 2)
(15873, 5)
(35151, 1)
(41277, 1)
(38871, 1)
(9438, 6)
(16526, 4)
(34113, 2)
(17721, 3)
(42835, 2)
(35127, 1)
(19467, 1)
(42191, 2)
(13459, 2)
(15069, 1)
(35495, 7)
(39691, 2)
(33237, 4)
(20003, 3)
(35173, 1)
(36036, 3)
(30138, 2)
(33078, 4)
(40365, 3)
(31547, 4)
(34225, 1)
(35093, 2)
(35489, 2)
(39145, 1)
(35035, 2)
(42183, 4)
(35098, 1)
(39103, 1)
(22973, 4)
(37878, 1)
(34191, 2)
(35162, 1)
(28561, 1)
(35154, 1)
(27681, 2)
(33824, 1)
(29733, 3)
(28017, 1)
(27961, 1)
(35020, 1)
(25607, 2)
(22523, 3)
(27379, 5)
(34718, 1)
(43684, 1)
(43729, 1)
(33

In [109]:
anime_freq_dict[1535]

57807

maybe change how closest user is calculated
how to get more niche animes in the recommendation when they dont have as much viewers?
    -increased weight based on ratings

In [113]:
test_freq_dict = {}
for review in ratings_target.itertuples():
    if review[2] in test_freq_dict:
        test_freq_dict[review[2]] += 1
    else:
        test_freq_dict[review[2]] = 1

In [115]:
test_freq_dict[1535]

1876

In [141]:
if "Action" in anime_df['Genders'][0]:
    print("yes")

yes


In [142]:
#Gets set of all genres
import re
re.split(r',\s', anime_df['Genders'][0])
genre_set = set()
for anime in anime_df['Genders']:
    genres = re.split(r',\s', anime)
    for genre in genres:
        genre_set.add(genre)
genre_set #44 total